In [1]:
import os
import sys
import random
import math
import numpy as np
import skimage.io
import matplotlib
import matplotlib.pyplot as plt
import cv2

import coco
from mrcnn import utils
from mrcnn import model as modellib
from mrcnn import visualize

Using TensorFlow backend.


In [2]:
ROOT_DIR = os.getcwd()
MODEL_DIR = os.path.join(ROOT_DIR, "logs")
COCO_MODEL_PATH = os.path.join(ROOT_DIR, "mask_rcnn_coco.h5")
# Download COCO trained weights from Releases if needed
if not os.path.exists(COCO_MODEL_PATH):
	utils.download_trained_weights(COCO_MODEL_PATH)
IMAGE_DIR = os.path.join(ROOT_DIR, "../../../train")
SAVE_DIR_BLACK = os.path.join(ROOT_DIR, "new_black_train")
SAVE_DIR_CROP = os.path.join(ROOT_DIR, "new_crop_train")


In [3]:
class InferenceConfig(coco.CocoConfig):
	# Set batch size to 1 since we'll be running inference on
	# one image at a time. Batch size = GPU_COUNT * IMAGES_PER_GPU
	GPU_COUNT = 1
	IMAGES_PER_GPU = 1

config = InferenceConfig()
config.display()


Configurations:
BACKBONE                       resnet101
BACKBONE_STRIDES               [4, 8, 16, 32, 64]
BATCH_SIZE                     1
BBOX_STD_DEV                   [ 0.1  0.1  0.2  0.2]
DETECTION_MAX_INSTANCES        100
DETECTION_MIN_CONFIDENCE       0.7
DETECTION_NMS_THRESHOLD        0.3
GPU_COUNT                      1
GRADIENT_CLIP_NORM             5.0
IMAGES_PER_GPU                 1
IMAGE_MAX_DIM                  1024
IMAGE_META_SIZE                93
IMAGE_MIN_DIM                  800
IMAGE_MIN_SCALE                0
IMAGE_RESIZE_MODE              square
IMAGE_SHAPE                    [1024 1024    3]
LEARNING_MOMENTUM              0.9
LEARNING_RATE                  0.001
LOSS_WEIGHTS                   {'rpn_class_loss': 1.0, 'rpn_bbox_loss': 1.0, 'mrcnn_bbox_loss': 1.0, 'mrcnn_mask_loss': 1.0, 'mrcnn_class_loss': 1.0}
MASK_POOL_SIZE                 14
MASK_SHAPE                     [28, 28]
MAX_GT_INSTANCES               100
MEAN_PIXEL                     [ 123.7  116.8

In [4]:
# Create model object in inference mode.
model = modellib.MaskRCNN(mode="inference", model_dir=MODEL_DIR, config=config)

# Load weights trained on MS-COCO
model.load_weights(COCO_MODEL_PATH, by_name=True)

In [5]:
class_names = ['BG', 'person', 'bicycle', 'car', 'motorcycle', 'airplane',
			   'bus', 'train', 'truck', 'boat', 'traffic light',
			   'fire hydrant', 'stop sign', 'parking meter', 'bench', 'bird',
			   'cat', 'dog', 'horse', 'sheep', 'cow', 'elephant', 'bear',
			   'zebra', 'giraffe', 'backpack', 'umbrella', 'handbag', 'tie',
			   'suitcase', 'frisbee', 'skis', 'snowboard', 'sports ball',
			   'kite', 'baseball bat', 'baseball glove', 'skateboard',
			   'surfboard', 'tennis racket', 'bottle', 'wine glass', 'cup',
			   'fork', 'knife', 'spoon', 'bowl', 'banana', 'apple',
			   'sandwich', 'orange', 'broccoli', 'carrot', 'hot dog', 'pizza',
			   'donut', 'cake', 'chair', 'couch', 'potted plant', 'bed',
			   'dining table', 'toilet', 'tv', 'laptop', 'mouse', 'remote',
			   'keyboard', 'cell phone', 'microwave', 'oven', 'toaster',
			   'sink', 'refrigerator', 'book', 'clock', 'vase', 'scissors',
			   'teddy bear', 'hair drier', 'toothbrush']

In [6]:

# Load images from the images folder
file_names = next(os.walk(IMAGE_DIR))[2]
BSIZE = 1000
STARTPOINT = 0
img_names = []
images = []

with open('labels.csv') as labels:
	for label in labels:
		label = label.strip()
		label = label.split(',')
		if label[0] == 'id':
			continue
		img_names.append(label)


for b in range(len(img_names)):
	if b < STARTPOINT:
		continue
	img_path = os.path.join(IMAGE_DIR, img_names[b][0]+'.jpg')
	print(img_path)
	image = skimage.io.imread(img_path)

	results = model.detect([image], verbose=1)
	result = results[0]

	rois = result['rois']
	masks = result['masks']
	class_ids = result['class_ids']
	scores = result['scores']
	print(scores)
	print(class_ids)
	num = class_ids.shape[0]
	c = False

	# class_id of the object to be cropped
	id = 17		# class id of dog
	list_dogs = []

	# To get the index of dog region with the highest score
	for i in range(num):
		if class_ids[i] == id:  	
			cp = image.copy()
			# Box
			y1, x1, y2, x2 = result['rois'][i]
			print(rois)
			print((y1,x1,y2,x2))
			cropped_img = cp[y1:y2, x1:x2]
			sav_path = os.path.join(SAVE_DIR_CROP, img_names[b][0])
			box = cropped_img.copy()

			# Mask
			# If pixel selected in mask - mask value 1
			# Otherwise - mask value 0
			mask = masks[:, :, i]
			row, col = image.shape[0], image.shape[1]
			for r in range(row):
			    for c in range(col):
			        if mask[r][c] == 0:
			            cp[r][c]=[0,0,0] 	# set unwanted pixels to be black in colour

			detected = cp[y1:y2, x1:x2]		# crop the image according to the box
			sav_path = os.path.join(SAVE_DIR_BLACK, img_names[b][0])
			list_dogs.append( (abs(y2-y1)*abs(x2-x1),box,detected ) )
			c = True
	if(c == False):
		image_d = skimage.io.imread(os.path.join(IMAGE_DIR, img_names[b][0]+'.jpg'))
		sav_path = os.path.join(SAVE_DIR_CROP, img_names[b][0])
		skimage.io.imsave(sav_path+'.jpg', image_d)
		sav_path = os.path.join(SAVE_DIR_BLACK, img_names[b][0])
		skimage.io.imsave(sav_path+'.jpg', image_d)
		print(str(b) + "original images finished!")
		continue
	sorted_dogs = sorted(list_dogs, key = lambda x:x[0], reverse = True)
	sav_path = os.path.join(SAVE_DIR_CROP, img_names[b][0])
	skimage.io.imsave(sav_path+'.jpg', sorted_dogs[0][1])
	sav_path = os.path.join(SAVE_DIR_BLACK, img_names[b][0])
	skimage.io.imsave(sav_path+'.jpg', sorted_dogs[0][2])


	print(str(b) + " images finished!")

C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\000bec180eb18c7604dcecc8fe0dba07.jpg
Processing 1 images
image                    shape: (375, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  145.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99949431  0.85420644]
[17 54]
[[  0 117 307 254]
 [ 23 155 364 497]]
(0, 117, 307, 254)
0 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\001513dfcb2ffafc82cccf4d8bbaba97.jpg
Processing 1 images
image                    shape: (375, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas

[ 0.93827474  0.89741057]
[17 58]
[[  8 102 295 408]
 [ 10   6 275 207]]
(8, 102, 295, 408)
12 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\006cc3ddb9dc1bd827479569fcdc52dc.jpg
Processing 1 images
image                    shape: (223, 250, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99671954]
[17]
[[  5  27 215 245]]
(5, 27, 215, 245)
13 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\0075dc49dab4024d12fafe67074d8a81.jpg
Processing 1 images
image                    shape: (332, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shap

molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99186301  0.95143682  0.89144588  0.89068156  0.79468989]
[63 57 17 17 16]
[[ 56 444 149 498]
 [ 96 333 123 384]
 [ 70  93 178 293]
 [ 57  28 370 483]
 [ 75   0 369 464]]
(70, 93, 178, 293)
[[ 56 444 149 498]
 [ 96 333 123 384]
 [ 70  93 178 293]
 [ 57  28 370 483]
 [ 75   0 369 464]]
(57, 28, 370, 483)
25 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\00a862390341c5be090dd72bd2bc19ef.jpg
Processing 1 images
image                    shape: (500, 375, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93) 

[ 0.99988425  0.99677891  0.99280518]
[17 57 61]
[[ 37 140 263 489]
 [  2   5 179 133]
 [171   1 326 500]]
(37, 140, 263, 489)
37 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\010d65bd29d246aea53d9849da142ccf.jpg
Processing 1 images
image                    shape: (500, 375, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.9974668   0.78841829]
[17 37]
[[  2  69 451 337]
 [316  61 483 282]]
(2, 69, 451, 337)
38 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\010e87fdf252645a827e37470e65e842.jpg
Processing 1 images
image                    shape: (361, 500, 3)         

[ 0.99490064  0.85010731]
[17 17]
[[ 65  78 181 183]
 [ 96 147 178 275]]
(65, 78, 181, 183)
[[ 65  78 181 183]
 [ 96 147 178 275]]
(96, 147, 178, 275)
50 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\0159b6457aac89f43d1c1931cdf7500b.jpg
Processing 1 images
image                    shape: (375, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[]
[]
51original images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\015b363b062f602e7ec04ce28e640d05.jpg
Processing 1 images
image                    shape: (288, 288, 3)         min:    0.00000  max:  255.00000  uint8
molded_images

...

[ 0.91055715  0.86130333  0.83695942  0.78725773  0.71136457]
[51 20 51 22 59]
10159original images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\fe5e4ee18529af1af1861efd550561a3.jpg
Processing 1 images
image                    shape: (333, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99905723]
[17]
[[ 35  37 293 302]]
(35, 37, 293, 302)
10160 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\fe624532170510bd80627c0500bafc97.jpg
Processing 1 images
image                    shape: (300, 400, 3)         min:    0.00000  max:  247.00000  uint8
molded_images            sh

[ 0.99973458]
[17]
[[233 230 805 989]]
(233, 230, 805, 989)
10172 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\fede60fb2acc02a2da0d0a05f760b7d5.jpg
Processing 1 images
image                    shape: (250, 250, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  147.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99881822  0.89855081]
[17 30]
[[ 68  49 202 212]
 [  0  76  41 217]]
(68, 49, 202, 212)
10173 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\fee1696ae6725863f84b0da2c05ad892.jpg
Processing 1 images
image                    shape: (375, 500, 3)         min:   20.00000  max:  255.00000  uint8
molded_images       

10185 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\ff0def9dafea6e633d0d7249554fcb2c.jpg
Processing 1 images
image                    shape: (342, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99830866  0.99540722]
[17 17]
[[ 80  64 331 217]
 [ 12 247 214 361]]
(80, 64, 331, 217)
[[ 80  64 331 217]
 [ 12 247 214 361]]
(12, 247, 214, 361)
10186 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\ff12508818823987d04e8fa4f5907efe.jpg
Processing 1 images
image                    shape: (263, 350, 3)         min:    0.00000  max:  255.00000  uint8
molded_images        

10197 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\ff6f47aa8e181b6efa4d0be7b09b5628.jpg
Processing 1 images
image                    shape: (333, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99869752]
[17]
[[  7 102 333 384]]
(7, 102, 333, 384)
10198 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\ff7334b06cee8667a7f30eb00e0b93cf.jpg
Processing 1 images
image                    shape: (330, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas       

[ 0.85781115  0.78207815]
[18 17]
[[ 188   85 1166  803]
 [ 156   62 1158  815]]
(156, 62, 1158, 815)
10210 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\ffc2b6b9133a6413c4a013cff29f9ed2.jpg
Processing 1 images
image                    shape: (332, 500, 3)         min:    0.00000  max:  255.00000  uint8
molded_images            shape: (1, 1024, 1024, 3)    min: -123.70000  max:  151.10000  float64
image_metas              shape: (1, 93)               min:    0.00000  max: 1024.00000  float64
anchors                  shape: (1, 261888, 4)        min:   -0.35390  max:    1.29134  float32
[ 0.99872762  0.8750006 ]
[17  1]
[[ 33  22 331 407]
 [  0 338 321 495]]
(33, 22, 331, 407)
10211 images finished!
C:\Users\Zhiye\Desktop\4995\project\code\4995deepLearningFinalProject\Mask R-CNN\../../../train\ffc532991d3cd7880d27a449ed1c4770.jpg
Processing 1 images
image                    shape: (375, 500, 3)         min:    0.00000  m